## e621.net/e6ai.net JSON to `.txt` tags
----

This Python script is designed to process JSON files found within a specified directory and its subdirectories. Each JSON file is expected to contain data related to image posts, particularly sourced from online platforms such as image boards. The script parses these JSON files, extracts relevant information such as image URL, ratings, and tags, and generates caption files (`.txt`) based on this data.

Here's a breakdown of what the script does:

1. **Ignoring Tags**: The script defines a list of tags to be ignored during processing, such as "hi res", "shaded", etc.

2. **Processing Files**: The `process_file` function is responsible for processing each JSON file. It reads the JSON data, extracts the URL of the image file, determines its rating, and extracts tags associated with the image.

3. **Generating Caption File**: For each image, a caption file is generated with the same name as the image file but with a .txt extension. The rating of the image is written first, followed by processed tags.

4. **Processing Tags**: Tags are processed to replace underscores with spaces and to handle special cases such as artist tags. Ignored tags are filtered out.

In [1]:
"""
Define tags to be ignored using regular expressions for exact matching
"""
ignored_tags = [r"\bblizzard entertainment\b", r"\bwarcraft\b",
    r"(?:\d{4})|(?:\d+:\d+)",
    r"\bdetailed\b", r"\bwidescreen\b", r"\b4k\b",
    r"\babsurd res\b", r"\bhi res\b", r"\bshaded\b",  r"\bdetailed\b",
    r"\btagme\b",
    r"\bdota\b",
    r"\bcreative commons\b", r"\bcc-by-nc-nd\b",
    r"\bsquare enix\b", r"\bfinal fantasy xiv\b", r"\bfinal fantasy\b",
    r"\bmythological canine\b", r"\basian mythology\b", r"\bmythological scalie\b",
    r"\bancient pokemon\b", r"\bmythological creature\b", r"\blegendary pokemon\b",
    r"\bfelis\b", r"\bfelid\b",
    r"\bsega\b",
    r"\bhasbro\b",
    r"\bzootopia\b",
    r"\bfive nights at freddy's\b",
    r"\beeveelution\b",
    r"\bdisney\b",
    r"\bmammal\b", r"\bcanis\b", r"\bcanine\b", r"\bcanid\b",
    r"\bdigimon\b", r"\bbandai namco\b",
    r"\bpokemon (species)\b",
    r"\bpal (species)\b",
    r"\bpokemon\b", r"\bnintendo\b",
    r"\\bby conditional dnp\\b",
    r"\\bconditional dnp\\b",
    r"\\bconditional_dnp\\b",
    r"\\bby\\s+conditional\\s+dnp\\b",
    r"\bgeneration\s+\d+\s+pokemon\b",
]

In [2]:
import os
import glob
import re
import json
from rich.console import Console
from rich.table import Table

console = Console()


def should_ignore_tag(tag, all_tags):
    for ignored_tag_pattern in ignored_tags:
        pattern = re.compile(ignored_tag_pattern, re.VERBOSE | re.IGNORECASE)
        if any(re.search(pattern, t) for t in all_tags):
            return True
    return False


def process_tags(tags_dict):
    processed_tags = []
    for category, tags_list in tags_dict.items():
        category_tags = []
        if category == "artist":
            category_tags = [
                f"by {tag.replace('_', ' ').replace(' (artist)', '')}"
                for tag in tags_list
                if tag
            ]
        else:
            for tag in tags_list:
                tag = tag.replace("_", " ")
                tag = re.sub(r"(?<!\\)\(", r"\(", tag)
                tag = re.sub(r"(?<!\\)\)", r"\)", tag)
                if tag.lower() == "artist":
                    continue
                if not should_ignore_tag(tag, tags_list):
                    category_tags.append(tag)
        processed_tags.extend(category_tags)
    return processed_tags

def process_file(file_path):
    try:
        console.print(f"Processing file: [bold]{file_path}[/bold]")
        with open(file_path, "r") as f:
            data = json.load(f)
        # Parse the URL and generate filename
        post_data = data.get("post", {})
        file_data = post_data.get("file", {})
        url = file_data.get("url")
        if url:
            filename, ext = os.path.splitext(os.path.basename(url))
            # Create caption file
            caption_file = f"{filename}.txt"
            caption_path = os.path.join(os.path.dirname(file_path), caption_file)
            with open(caption_path, "w", encoding="utf-8") as f:
                # Write rating
                rating = post_data.get("rating", "q")
                if rating == "s":
                    f.write("rating_safe, ")
                elif rating == "e":
                    f.write("rating_explicit, ")
                else:
                    f.write("rating_questionable, ")
                # Process tags
                tags_data = post_data.get("tags", {})
                processed_tags = process_tags(tags_data)
                # Check if there are any valid tags before writing
                if processed_tags:
                    # Join tags with commas and write to file
                    tags_line = ", ".join(processed_tags)
                    f.write(tags_line.strip())

                    # Create a table
                    table = Table(show_header=True, header_style="bold magenta")
                    table.add_column(caption_path, justify="center")

                    table.add_row(tags_line.strip())

                    # Print the table
                    console.print(table)
    except Exception as e:
        console.print(f"Error processing file: [bold]{file_path}[/bold]")
        console.print(e)


def recursive_process(directory):
    for file_path in glob.glob(directory + "/**/*.json", recursive=True):
        process_file(file_path)


if __name__ == "__main__":
    #root_directory = r"E:\training_dir"
    root_directory = r"E:\training_dir_staging"
    recursive_process(root_directory)

Processing file: E:\training_dir_staging\package-lock.json

Processing file: E:\training_dir_staging\package.json

Processing file: E:\training_dir_staging\2_anthro_weasel\3051834.json

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃                  E:\training_dir_staging\2_anthro_weasel\8a5ed4f684745414e5e57b2e3c9276ff.txt                   ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│    4 toes, anthro, balls, bandanna, blush, brown body, brown fur, chastity cage, chastity device, clothing,     │
│  dialogue, dildo, exclamation point, feet, fur, genitals, hair, hindpaw, kerchief, legs up, lying, male, male   │
│  wearing strapon, masturbation, mostly nude, offscreen character, on back, pawpads, paws, penetrable sex toy,   │
│    penis, pink background, pouting, question mark, sex toy, simple background, solo, speech bubble, strapon,    │
│    strapon masturbation, strapon over chastity, strapon over penis, tan body, tan fur, teasing, text, toes,     │
│        underwear, white hair, by bittenbun, merlin \(lllmaddy\), digital media \(artwork\), english text        │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

Processing file: E:\training_dir_staging\2_anthro_weasel\3584444.json

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃                  E:\training_dir_staging\2_anthro_weasel\ecff451612ee44a571db893d44c910ce.txt                   ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│  anthro, anus, athletic, athletic anthro, athletic male, backsack, balls, big penis, butt, chandelier, claws,   │
│  crouching, erection, eyebrows, fur, genitals, hair, humanoid genitalia, humanoid penis, imminent facesitting,  │
│  indoor nudity, inside, licking, licking lips, licking own lips, looking at viewer, looking down, looking down  │
│ at viewer, low-angle view, male, nipples, nude, nude anthro, nude male, open mouth, open smile, pawpads, pecs,  │
│   penis, perineum, presenting, presenting anus, presenting hindquarters, presenting penis, self lick, smile,    │
│           solo, teeth, thick thighs, tongue, tongue out, tuft, worm's-eye view, by kihu, barnaby kane           │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

Processing file: E:\training_dir_staging\2_anthro_weasel\4264190.json

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃                  E:\training_dir_staging\2_anthro_weasel\3394ff7098766b5d13ff9728f8178895.txt                   ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│    4 toes, after sex, anthro, balls, beach, beach towel, beach umbrella, bedroom eyes, being watched, bodily    │
│ fluids, butt, claws, cloud, crowd, cum, cum covered, cum in ass, cum inside, cum on anus, cum on belly, cum on  │
│ body, cum on butt, cum on chest, cum on face, cum on feet, cum on head, cum on leg, cum on paw, cum on pawpads, │
│ cum on penis, cum on tail, erection, excessive cum, excessive genital fluids, exhibitionism, feet, fur, genital │
│    fluids, genitals, group, half-closed eyes, humanoid genitalia, humanoid penis, inner ear fluff, legs up,     │
│ looking at another, looking at viewer, male, male anthro, messy, narrowed eyes, nude, orange body, orange fur,  │
│  outdoor nudity, outside, parasol, pawpads, paws, penis, pinup, pose, presenting, presenting balls, presenting  │
│  penis, public, public nudity, realistic penis size, sand, seaside, seductive, sky, smile, smiling at viewer,   │
│            solo, spread legs, spreading, tail, toe claws, toes, towel, tuft, whiskers, by oxfort2199            │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

Processing file: E:\training_dir_staging\2_anthro_weasel\521244.json

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┓
┃                  E:\training_dir_staging\2_anthro_weasel\12e58e17f13c0e71cbe40059fb8cc169.txt                   ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┩
│ 4 toes, anal, anal penetration, animal genitalia, animal penis, anthro, anthro on anthro, balls, bodily fluids, │
│  canine genitalia, canine penis, claws, cum, cum in ass, cum inside, digitigrade, duo, erection, eyes closed,   │
│  eyewear, feet, finger fetish, finger in mouth, finger play, fingers, fur, genital fluids, genitals, glasses,   │
│     hindpaw, humanoid genitalia, humanoid penis, knot, licking, licking lips, lying, male, male/male, male      │
│ penetrated, male penetrating, male penetrating male, nude, on back, pawpads, paws, penetration, penis, precum,  │
│    self lick, sex, slightly chubby, soles, spread legs, spreading, toes, tongue, tongue out, white balls, by    │
│                       conditional dnp, by garnetto, arcshep, tre, tre \(milligram smile\)                       │
└─────────────────────────────────────────────────────────────────────────────────────────────────────────────────┘

## Delete every JSON file ⚠️

---

In [10]:
import glob
import os

def delete_json_files(directory):
    # Create the path pattern to match JSON files
    pattern = os.path.join(directory, '**', '*.json')
    
    # Find all JSON files using glob
    json_files = glob.glob(pattern, recursive=True)
    
    # Delete each JSON file
    for file_path in json_files:
        try:
            os.remove(file_path)
            print(f"Deleted: {file_path}")
        except OSError as e:
            print(f"Error deleting {file_path}: {e}")

if __name__ == "__main__":
    # Specify the directory path
    #directory_path = r'E:\training_dir'
    directory_path = r'C:\Users\kade\Desktop\training_dir_staging'

    # Call the function to delete JSON files recursively
    delete_json_files(directory_path)